In [1]:
#Libraries Installation
!pip install openai
!pip install sentence-transformers
!pip install langdetect

import openai
#Importing the dataset
import pandas as pd
import numpy as np


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.5/325.5 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 5.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 4.8 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (

In [2]:


from google.colab import drive
drive.mount('/content/drive')

segments_df = pd.read_excel("SauLTC_file_Health_Create_Segments.xlsx")
# Drop rows where either the English or Arabic column is NaN
segments_df.dropna(subset=['English Segment', 'Arabic Segment'], inplace=True)
segments_df.reset_index(drop=True, inplace=True)
segments_df

Mounted at /content/drive


English Segment  \
0    step 1 inform yourself If you or a loved one h...   
1    In fact, Hippocrates first described and named...   
2    how cancer develops ‘Solid’ tumours that devel...   
3    Embryonic stem cells, the cells found in the v...   
4    A powerful example of the impact of gene expre...   
..                                                 ...   
464  But this was for the whole city – not just for...   
465  But it doesn’t leave much time for decision th...   
466  Jesse is not. Occasionally, when he thinks I’m...   
467  Please skip ahead. But for a lot of us, we’re ...   
468  When we did start thinking more seriously abou...   

                                        Arabic Segment  Document_ID  
0    الخطوة الأولى ثقف نفسك اذا تم تشخيصك أو تشخيص ...            0  
1    فأبقراط في الواقع هو أول من وصفه وأسماه في الي...            0  
2    كيف ينشأ السرطان تمر الأورام الصلبة التي تظهر ...            0  
3    الخلايا الجذعية الجنينية ــ هي الخلايا التي تت...            0  
4    ويعد اليُسْرُوع والفراشة من الأمثلة القوية على...            0  
..                                                 ...          ...  
464  فكلُ ما كانَ علينا فعلُه ، أخذُ السعرِ القديم ...           84  
465  فأُخبرتُ فورًا بأنهُ بإمكاني شرب كوبين من القه...           84  
466  وعندما يتوقع جيسي أحيانًا أنني لا أبحث عنه ، أ...           84  
467  ولكن نحن غالبًا ما نفكر بالحمل قبل أن نحمل بوق...           84  
468  وعندما أفكر جديا بإنجاب طفل ، فإن تفكيري يتمحو...           84  

[469 rows x 3 columns]

In [3]:
import re
from langdetect import detect, LangDetectException

def chat_with_gpt(prompt, model="gpt-3.5-turbo-16k", api_key="Your_key"):
    openai.api_key = api_key

    try:
        response = openai.chat.completions.create(
            model=model,
            messages=[
                {"role": "system", "content": "Format each pair as 'English: [English Text] \\nArabic: [Arabic Text]'. Separate each sentence pair with a newline."},
                {"role": "user", "content": prompt}
            ],
            temperature=0.4,
            top_p=0.7
        )
        return response.choices[0].message.content
    except Exception as e:
        return str(e)

def is_mostly_language(text, expected_lang):
    if expected_lang == 'en':
        # Count Latin characters as a proxy for English content
        latin_chars = sum('A' <= c <= 'Z' or 'a' <= c <= 'z' for c in text)
        return latin_chars > len(text) / 2
    elif expected_lang == 'ar':
        # Count Arabic characters as a proxy for Arabic content
        arabic_chars = sum('\u0600' <= c <= '\u06FF' or '\u0750' <= c <= '\u077F' or '\u08A0' <= c <= '\u08FF' or '\uFB50' <= c <= '\uFDFF' or '\uFE70' <= c <= '\uFEFF' for c in text)
        return arabic_chars > len(text) / 2
    return False

def is_language(text, expected_lang):
    try:
        detected_lang = detect(text)
        if detected_lang == expected_lang:
            return True
    except LangDetectException:
        pass  # Proceed to heuristic check if detection fails

    # Use a heuristic check as a fallback
    return is_mostly_language(text, expected_lang)

def is_correct_order_and_content_with_language_check(text):
    segments = []
    current_segment = ''
    for line in text.split('\n'):
        if line.startswith("English:") or line.startswith("Arabic:"):
            if current_segment:
                segments.append(current_segment.strip())
            current_segment = line
        else:
            current_segment += ' ' + line
    if current_segment:
        segments.append(current_segment.strip())

    for segment in segments:
        if segment.startswith("English:"):
            content = segment[len("English:"):].strip()
            if not is_language(content, 'en'):
                return False
        elif segment.startswith("Arabic:"):
            content = segment[len("Arabic:"):].strip()
            if not is_language(content, 'ar'):
                return False

    return True

def process_text(text):

    # Use regex to find all instances of "English:" possibly followed by whitespace and the end of the string
    english_pattern = r"English:\s*$"

    # If the pattern is found at the end of the text, remove it
    if re.search(english_pattern, text):
        text = re.sub(english_pattern, '', text)

    # Count occurrences of "English:" and "Arabic:"
    e_count = text.count("English: ")
    a_count = text.count("Arabic: ")
    # Return the processed text and counts
    return text, e_count, a_count


In [4]:
# PART 1
not_correct = []
new_rows = []
Translation_df_aligned=pd.DataFrame(columns = ['Text','Document_ID'])
df_not_correct = pd.DataFrame(columns = ['Text','Document_ID'])

# Main loop to process each segment
for index, row in segments_df.iloc[0:100].iterrows():
    print(f"Processing document {index}")
    prompt = f"For the English text: {row['English Segment']} and its corresponding Arabic translation text: {row['Arabic Segment']}, perform the following steps:\n1. Segment all the English text and its corresponding Arabic translation into sentences.\n2. Then, Align all English sentence with its corresponding Arabic sentence."
    response, e_count, a_count = process_text(chat_with_gpt(prompt))
    if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
      print(response)
      response, e_count, a_count = process_text(chat_with_gpt(prompt))
      if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
        print(response)
        not_correct.append({'Text':response, 'Document_ID': row['Document_ID']})
      else:
        new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
    else:
      new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
# Convert lists to DataFrames
Translation_df_aligned = pd.DataFrame(new_rows)
df_not_correct = pd.DataFrame(not_correct)

# Saving DataFrames to Excel files (Adjust the path as needed)
Translation_df_aligned.to_excel("Translation_df_aligned_GPT3_version5_part1.xlsx", index=False)
df_not_correct.to_excel("df_not_correct_version5_part_1.xlsx", index=False)


Processing document 0
Processing document 1
Processing document 2
Processing document 3
Processing document 4
English: A powerful example of the impact of gene expression is the caterpillar and the butterfly.
Arabic: مثال قوي على تأثير التعبير الجيني هو اليرقة والفراشة.

English: Both have exactly the same set of genes.
Arabic: كلاهما يمتلكان نفس المجموعة الكاملة من المورثات.

English: In the larval stage, the pattern of gene expression forms a caterpillar.
Arabic: في المرحلة اليرقانية، يشكل نمط التعبير الجيني يُسْرُوع.

English: But then in the adult, following pupation, different organisation of the same genes results in changed from which produces a beautiful butterfly.
Arabic: ولكن بعد ذلك في مرحلة البلوغ، بعد التشرنق، يؤدي تنظيم مختلف لنفس المورثات إلى تغير ينتج عنه فراشة جميلة.

English: If differences in the expression of the same set of genes can give such extraordinarily diverse results as the caterpillar and the butterfly, it is easy to see that the processes that control gen

In [ ]:
# PART 2
not_correct = []
new_rows = []
Translation_df_aligned=pd.DataFrame(columns = ['Text','Document_ID'])
df_not_correct = pd.DataFrame(columns = ['Text','Document_ID'])

# Main loop to process each segment
for index, row in segments_df.iloc[100:200].iterrows():
    print(f"Processing document {index}")
    prompt = f"For the English text: {row['English Segment']} and its corresponding Arabic translation text: {row['Arabic Segment']}, perform the following steps:\n1. Segment all the English text and its corresponding Arabic translation into sentences.\n2. Then, Align all English sentence with its corresponding Arabic sentence."
    response, e_count, a_count = process_text(chat_with_gpt(prompt))
    if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
      print(response)
      response, e_count, a_count = process_text(chat_with_gpt(prompt))
      if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
        print(response)
        not_correct.append({'Text':response, 'Document_ID': row['Document_ID']})
      else:
        new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
    else:
      new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
# Convert lists to DataFrames
Translation_df_aligned = pd.DataFrame(new_rows)
df_not_correct = pd.DataFrame(not_correct)

# Saving DataFrames to Excel files (Adjust the path as needed)
Translation_df_aligned.to_excel("Translation_df_aligned_GPT3_version5_part2.xlsx", index=False)
df_not_correct.to_excel("df_not_correct_version5_part_2.xlsx", index=False)


In [ ]:
# PART 3
not_correct = []
new_rows = []
Translation_df_aligned=pd.DataFrame(columns = ['Text','Document_ID'])
df_not_correct = pd.DataFrame(columns = ['Text','Document_ID'])

# Main loop to process each segment
for index, row in segments_df.iloc[200:300].iterrows():
    print(f"Processing document {index}")
    prompt = f"For the English text: {row['English Segment']} and its corresponding Arabic translation text: {row['Arabic Segment']}, perform the following steps:\n1. Segment all the English text and its corresponding Arabic translation into sentences.\n2. Then, Align all English sentence with its corresponding Arabic sentence."
    response, e_count, a_count = process_text(chat_with_gpt(prompt))
    if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
      print(response)
      response, e_count, a_count = process_text(chat_with_gpt(prompt))
      if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
        print(response)
        not_correct.append({'Text':response, 'Document_ID': row['Document_ID']})
      else:
        new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
    else:
      new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
# Convert lists to DataFrames
Translation_df_aligned = pd.DataFrame(new_rows)
df_not_correct = pd.DataFrame(not_correct)

# Saving DataFrames to Excel files (Adjust the path as needed)
Translation_df_aligned.to_excel("Translation_df_aligned_GPT3_version5_part3.xlsx", index=False)
df_not_correct.to_excel("df_not_correct_version5_part_3.xlsx", index=False)


In [ ]:
# PART 4
not_correct = []
new_rows = []
Translation_df_aligned=pd.DataFrame(columns = ['Text','Document_ID'])
df_not_correct = pd.DataFrame(columns = ['Text','Document_ID'])

# Main loop to process each segment
for index, row in segments_df.iloc[300:].iterrows():
    print(f"Processing document {index}")
    prompt = f"For the English text: {row['English Segment']} and its corresponding Arabic translation text: {row['Arabic Segment']}, perform the following steps:\n1. Segment all the English text and its corresponding Arabic translation into sentences.\n2. Then, Align all English sentence with its corresponding Arabic sentence."
    response, e_count, a_count = process_text(chat_with_gpt(prompt))
    if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
      print(response)
      response, e_count, a_count = process_text(chat_with_gpt(prompt))
      if e_count != a_count or e_count == 0 or a_count == 0 or not is_correct_order_and_content_with_language_check(response):
        print(response)
        not_correct.append({'Text':response, 'Document_ID': row['Document_ID']})
      else:
        new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
    else:
      new_rows.append({'Text':response, 'Document_ID': row['Document_ID']})
# Convert lists to DataFrames
Translation_df_aligned = pd.DataFrame(new_rows)
df_not_correct = pd.DataFrame(not_correct)

# Saving DataFrames to Excel files (Adjust the path as needed)
Translation_df_aligned.to_excel("Translation_df_aligned_GPT3_version5_part4.xlsx", index=False)
df_not_correct.to_excel("df_not_correct_version5_part_4.xlsx", index=False)


In [ ]:
import pandas as pd
from google.colab import drive
drive.mount('/content/drive')

# Read the Excel file into a DataFrame
df_1 = pd.read_excel('Translation_df_aligned_GPT3_version5_part1.xlsx')
df_2 = pd.read_excel('Translation_df_aligned_GPT3_version5_part2.xlsx')
df_3 = pd.read_excel('Translation_df_aligned_GPT3_version5_part3.xlsx')
df_4 = pd.read_excel('Translation_df_aligned_GPT3_version5_part4.xlsx')

combined_df = pd.concat([df_1,df_2,df_3,df_4], ignore_index=True)
print(combined_df)

df_not_correct_1 = pd.read_excel("df_not_correct_version5_part_1.xlsx")
df_not_correct_2 = pd.read_excel("df_not_correct_version5_part_2.xlsx")
df_not_correct_3 = pd.read_excel("df_not_correct_version5_part_3.xlsx")
df_not_correct_4 = pd.read_excel("df_not_correct_version5_part_4.xlsx")
combined_not_correct = pd.concat([df_not_correct_1,df_not_correct_2,df_not_correct_3,df_not_correct_4], ignore_index=True)
print(combined_not_correct)
combined_not_correct.to_excel("combined_not_correct_version5.xlsx")

Mounted at /content/drive
                                                  Text  Document_ID
0    English: Step 1 inform yourself If you or a lo...            0
1    English: In fact, Hippocrates first described ...            0
2    English: How cancer develops ‘Solid’ tumours t...            0
3    English: Embryonic stem cells, the cells found...            0
4    English: A powerful example of the impact of g...            0
..                                                 ...          ...
421  English: But this was for the whole city – not...           84
422  English: But it doesn’t leave much time for de...           84
423  English: Jesse is not.\nArabic: جيسي ليس كذلك....           84
424  English: But for a lot of us, we’re thinking a...           84
425  English: When we did start thinking more serio...           84

[426 rows x 2 columns]
                                                 Text  Document_ID
0   English: 33\nArabic: والذي يعد ساما فتحتاج بذل...            0


In [ ]:
!pip install sentence_transformers
from sentence_transformers import SentenceTransformer, util
from sklearn.preprocessing import normalize
import numpy as np

model1 = SentenceTransformer("distiluse-base-multilingual-cased-v2")
model2 = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2")
model3 = SentenceTransformer("paraphrase-multilingual-mpnet-base-v2")
model4 = SentenceTransformer("LaBSE")


def evaluate_semantic_similarity(source_embeddings, translated_embeddings):
    """
    Evaluate semantic similarity between source sentences and their translations.
    :param source_sentences: List of source sentences in English.
    :param translated_sentences: List of translated sentences in Arabic.
    :param model_name: Name of the sentence transformer model.
    :return: List of cosine similarity scores for each sentence pair.
    """
    # Calculating cosine similarity
    similaritiy = util.pytorch_cos_sim(source_embeddings, translated_embeddings)
    return similaritiy



In [ ]:
Translation_df_aligned_SS=pd.DataFrame(columns = ['En', 'Ar','Document_ID','Similarity_Score1','Similarity_Score2','Similarity_Score3','Similarity_Score4'])

for i in range(len(combined_df)):
    print(i)
    segments = combined_df.Text[i].split("English:")
    segments = [seg.strip() for seg in segments if seg.strip() != ""]
    new_rows = []
    # Looping through the lines and adding them to the DataFrame
    for seg in segments:

        try:
            english, arabic = seg.split("Arabic:")
        except ValueError:
            english, arabic = seg, ""

        # Generating embeddings
        source_embeddings = model1.encode(english.strip().lower(), convert_to_tensor=True)
        translated_embeddings = model1.encode(arabic.strip().lower(), convert_to_tensor=True)
        score1 =evaluate_semantic_similarity(source_embeddings,translated_embeddings)

        source_embeddings = model2.encode(english.strip().lower(), convert_to_tensor=True)
        translated_embeddings = model2.encode(arabic.strip().lower(), convert_to_tensor=True)
        score2 =evaluate_semantic_similarity(source_embeddings,translated_embeddings)

        source_embeddings = model3.encode(english.strip().lower(), convert_to_tensor=True)
        translated_embeddings = model3.encode(arabic.strip().lower(), convert_to_tensor=True)
        score3 =evaluate_semantic_similarity(source_embeddings,translated_embeddings)

        source_embeddings = model4.encode(english.strip().lower(), convert_to_tensor=True)
        translated_embeddings = model4.encode(arabic.strip().lower(), convert_to_tensor=True)
        score4 =evaluate_semantic_similarity(source_embeddings,translated_embeddings)

        new_rows.append({'En': english.strip(), 'Ar': arabic.strip(), 'Document_ID': combined_df.Document_ID[i],'Similarity_Score1' : score1[0].item(),'Similarity_Score2' : score2[0].item(),'Similarity_Score3' : score3[0].item(),'Similarity_Score4' : score4[0].item()})

    Translation_df_aligned_SS = pd.concat([Translation_df_aligned_SS, pd.DataFrame(new_rows)], ignore_index=True)
Translation_df_aligned_SS.to_excel("Evaluation_GPT3_version5.xlsx", index=False)


# Filter the DataFrame
Translation_df_aligned_SS = Translation_df_aligned_SS.drop_duplicates(subset='En')
Translation_df_aligned_SS = Translation_df_aligned_SS.drop_duplicates(subset='Ar')
Translation_df_aligned_SS = Translation_df_aligned_SS[~Translation_df_aligned_SS['En'].str.lower().str.startswith("and its corresponding arabic translation text:")]
Translation_df_aligned_SS.reset_index(drop=True, inplace=True)
Translation_df_aligned_SS.to_excel("Evaluation_GPT3_version5_after filter.xlsx", index=False)


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [ ]:
Translation_df_aligned_SS["Similarity_Score1"].mean()
#0.8232530435003035

0.8232530435003035

In [ ]:
Translation_df_aligned_SS["Similarity_Score2"].mean()
#0.8234694008220277

0.8234694008220277

In [ ]:
Translation_df_aligned_SS["Similarity_Score3"].mean()
#0.8610441401829038

0.8610441401829038

In [ ]:
Translation_df_aligned_SS["Similarity_Score4"].mean()
#0.8499381928810876

0.8499381928810876